### Setup some basic stuff

In [1]:
import logging
logging.getLogger().setLevel(logging.DEBUG)

In [2]:
import folium
import folium.features as fof
import folium.utilities as ful
import branca.element as bre
import json
import geojson as gj
import arrow

import shapely.geometry as shpg
import pandas as pd
import geopandas as gpd

In [3]:
def lonlat_swap(lon_lat):
    return list(reversed(lon_lat))

In [4]:
def get_row_count(n_maps, cols):
    rows = (n_maps / cols)
    if (n_maps % cols != 0):
        rows = rows + 1
    return rows

In [5]:
def get_one_marker(loc, disp_color):
    if loc["geometry"]["type"] == "Point":
        curr_latlng = lonlat_swap(loc["geometry"]["coordinates"])
        return folium.Marker(curr_latlng, icon=folium.Icon(color=disp_color),
                  popup="%s" % loc["properties"]["name"])
    elif loc["geometry"]["type"] == "Polygon":
        assert len(loc["geometry"]["coordinates"]) == 1,\
            "Only simple polygons supported!"
        curr_latlng = [lonlat_swap(c) for c in loc["geometry"]["coordinates"][0]]
        # print("Returning polygon for %s" % curr_latlng)
        return folium.PolyLine(curr_latlng, color=disp_color, fill=disp_color,
                  popup="%s" % loc["properties"]["name"])        

In [6]:
def get_marker(loc, disp_color):
    if type(loc) == list:
        return [get_one_marker(l, disp_color) for l in loc]
    else:
        print("Found single entry, is this expected?")
        return [get_one_marker(loc, disp_color)]

### Read the data

In [7]:
spec_to_validate = json.load(open("final_sfbayarea_filled_reroutes/train_bus_ebike_mtv_ucb.filled.reroute.json"))
sensing_configs = json.load(open("sensing_regimes.all.specs.json"))

### Validating the time range

In [8]:
print("Experiment runs from %s -> %s" % (arrow.get(spec_to_validate["start_ts"]), arrow.get(spec_to_validate["end_ts"])))
start_fmt_time_to_validate = arrow.get(spec_to_validate["start_ts"]).format("YYYY-MM-DD")
end_fmt_time_to_validate = arrow.get(spec_to_validate["end_ts"]).format("YYYY-MM-DD")
if (start_fmt_time_to_validate != spec_to_validate["start_fmt_date"]):
    print("VALIDATION FAILED, got start %s, expected %s" % (start_fmt_time_to_validate, spec_to_validate["start_fmt_date"]))
if (end_fmt_time_to_validate != spec_to_validate["end_fmt_date"]):
    print("VALIDATION FAILED, got end %s, expected %s" % (end_fmt_time_to_validate, spec_to_validate["end_fmt_date"]))

Experiment runs from 2019-07-16T07:00:00+00:00 -> 2020-04-30T07:00:00+00:00


### Validating calibration trips

In [9]:
def get_map_for_calibration_test(trip):
    curr_map = folium.Map()
    if trip["start_loc"] is None or trip["end_loc"] is None:
        return curr_map
    curr_start = lonlat_swap(trip["start_loc"]["coordinates"])
    curr_end = lonlat_swap(trip["end_loc"]["coordinates"])
    folium.Marker(curr_start, icon=folium.Icon(color="green"),
                  popup="Start: %s" % trip["start_loc"]["name"]).add_to(curr_map)
    folium.Marker(curr_end, icon=folium.Icon(color="red"),
                  popup="End: %s" % trip["end_loc"]["name"]).add_to(curr_map)
    folium.PolyLine([curr_start, curr_end], popup=trip["id"]).add_to(curr_map)
    curr_map.fit_bounds([curr_start, curr_end])    
    return curr_map

In [10]:
calibration_tests = spec_to_validate["calibration_tests"]
rows = get_row_count(len(calibration_tests), 4)
calibration_maps = bre.Figure((rows,4))
for i, t in enumerate(calibration_tests):
    if t["config"]["sensing_config"] != sensing_configs[t["config"]["id"]]["sensing_config"]:
        print("Mismatch in config for test" % t)
    curr_map = get_map_for_calibration_test(t)
    calibration_maps.add_subplot(rows, 4, i+1).add_child(curr_map)
calibration_maps

### Validating evaluation trips

In [11]:
def add_waypoint_markers(waypoint_coords, curr_map):
    for i, wpc in enumerate(waypoint_coords["geometry"]["coordinates"]):
        folium.map.Marker(
            lonlat_swap(wpc), popup="%d" % i,
            icon=fof.DivIcon(class_name='leaflet-div-icon')).add_to(curr_map)

def get_map_for_travel_leg(trip):
    curr_map = folium.Map()
    [get_one_marker(loc, "green").add_to(curr_map) for loc in trip["start_loc"]]
    [get_one_marker(loc, "red").add_to(curr_map) for loc in trip["end_loc"]]
    
    # iterate over all reroutes
    for rc in trip["route_coords"]:
        coords = rc["geometry"]["coordinates"]
        print("Found %d coordinates for the route" % (len(coords)))
        
        latlng_coords = [lonlat_swap(c) for c in coords]
        folium.PolyLine(latlng_coords, popup="%s: %s" % (trip["mode"], trip["name"])).add_to(curr_map)
        
        for i, c in enumerate(latlng_coords):
            folium.CircleMarker(c, radius=5, popup="%d: %s" % (i, c)).add_to(curr_map)
            
        curr_map.fit_bounds(ful.get_bounds(latlng_coords))
    
    return curr_map

In [12]:
def get_map_for_shim_leg(trip):
    curr_map = folium.Map()
    for loc in trip["loc"]:
        mkr = get_one_marker(loc, "purple")
        mkr.add_to(curr_map)
        curr_map.fit_bounds(mkr.get_bounds())
    return curr_map

In [13]:
evaluation_trips = spec_to_validate["evaluation_trips"]
map_list = []
for t in evaluation_trips:
    for l in t["legs"]:
        if l["type"] == "TRAVEL":
            curr_map = get_map_for_travel_leg(l)
            map_list.append(curr_map)
        else:
            curr_map = get_map_for_shim_leg(l)
            map_list.append(curr_map)

rows = get_row_count(len(map_list), 2)
evaluation_maps = bre.Figure(ratio="{}%".format((rows/2) * 100))
for i, curr_map in enumerate(map_list):
    evaluation_maps.add_subplot(rows, 2, i+1).add_child(curr_map)
evaluation_maps

Found 89 coordinates for the route
Found 426 coordinates for the route
Found 626 coordinates for the route
Found 8 coordinates for the route
Found 9 coordinates for the route
Found 85 coordinates for the route
Found 67 coordinates for the route
Found 87 coordinates for the route
Found 78 coordinates for the route
Found 28 coordinates for the route
Found 42 coordinates for the route
Found 273 coordinates for the route
Found 266 coordinates for the route
Found 441 coordinates for the route
Found 408 coordinates for the route
Found 25 coordinates for the route
Found 29 coordinates for the route
Found 120 coordinates for the route
Found 701 coordinates for the route
Found 89 coordinates for the route


### Validating start and end polygons

In [16]:
def check_start_end_contains(leg):
    for rc in leg["route_coords"]:
        points = gpd.GeoSeries([shpg.Point(p) for p in rc["geometry"]["coordinates"]])
        
        route_start_date = arrow.get(rc["properties"]["valid_start_fmt_date"])
        route_end_date = arrow.get(rc["properties"]["valid_end_fmt_date"])
        
        # query all start_locs that have start date >= route start date and end date <= route end date
        start_locs = [shpg.shape(t["geometry"]) for t in leg["start_loc"]\
                      if arrow.get(t["properties"]["valid_start_fmt_date"]) >= route_start_date\
                      and arrow.get(t["properties"]["valid_end_fmt_date"]) <= route_end_date]
        
        # query all end_locs that have start date >= route start date and end date <= route end date
        end_locs = [shpg.shape(t["geometry"]) for t in leg["end_loc"]\
                    if arrow.get(t["properties"]["valid_start_fmt_date"]) >= route_start_date\
                    and arrow.get(t["properties"]["valid_end_fmt_date"]) <= route_end_date]
        
        for sl in start_locs:
            start_contains = points.apply(lambda p: sl.contains(p))
            print(points[start_contains])
            
            assert start_contains.any(), leg
            
            assert start_contains.iloc[0], points.head()
            
            max_index_diff_start = pd.Series(start_contains[start_contains == True].index).diff().max()
            assert pd.isnull(max_index_diff_start) or max_index_diff_start == 1, "Max diff in index = %s for points %s" % (gpd.GeoSeries(start_contains[end_contains == True].index).diff().max(), points.head())
            
        for el in end_locs:
            end_contains = points.apply(lambda p: el.contains(p))
            print(points[end_contains])
            
            assert end_contains.any(), leg
        
            assert end_contains.iloc[-1], points.tail()
        
            max_index_diff_end = pd.Series(end_contains[end_contains == True].index).diff().max()
            assert pd.isnull(max_index_diff_end) or max_index_diff_end == 1, "Max diff in index = %s for points %s" % (gpd.GeoSeries(end_contains[end_contains == True].index).diff().max(), points.tail())

In [17]:
invalid_legs = []
for t in evaluation_trips:
    for l in t["legs"]:
        if l["type"] == "TRAVEL" and l["id"] not in invalid_legs:
            print("Checking leg %s, %s" % (t["id"], l["id"]))
            check_start_end_contains(l)

Checking leg mtv_to_berkeley_sf_bart, walk_to_caltrain
0    POINT (-122.08337 37.39025)
1    POINT (-122.08338 37.39022)
dtype: geometry
83    POINT (-122.07657 37.39452)
84    POINT (-122.07652 37.39450)
85    POINT (-122.07649 37.39454)
86    POINT (-122.07601 37.39435)
87    POINT (-122.07604 37.39430)
88    POINT (-122.07573 37.39418)
dtype: geometry
Checking leg mtv_to_berkeley_sf_bart, commuter_rail_aboveground
0    POINT (-122.07630 37.39460)
1    POINT (-122.07667 37.39474)
dtype: geometry
425    POINT (-122.38759 37.60071)
dtype: geometry
Checking leg mtv_to_berkeley_sf_bart, subway_underground
0    POINT (-122.38606 37.59948)
dtype: geometry
624    POINT (-122.26803 37.86947)
625    POINT (-122.26829 37.87122)
dtype: geometry
Checking leg mtv_to_berkeley_sf_bart, walk_to_bus
6    POINT (-122.26771 37.87105)
7    POINT (-122.26771 37.87110)
dtype: geometry
GeoSeries([], dtype: geometry)


AssertionError: {'id': 'walk_to_bus', 'name': 'Walk from BART station to shuttle bus stop', 'mode': 'WALKING', 'start_loc': [{'type': 'Feature', 'properties': {'name': 'Downtown Berkeley BART', 'valid_start_fmt_date': '2019-07-16', 'valid_end_fmt_date': '2020-04-30'}, 'geometry': {'type': 'Polygon', 'coordinates': [[[-122.26870179176329, 37.871262515520044], [-122.26839065551758, 37.86921292650199], [-122.2675323486328, 37.869280682422094], [-122.26801514625548, 37.87133026955532], [-122.26870179176329, 37.871262515520044]]]}}], 'end_loc': [{'type': 'Feature', 'properties': {'name': 'Addison and Shattuck', 'valid_start_fmt_date': '2019-07-16', 'valid_end_fmt_date': '2019-12-31'}, 'geometry': {'type': 'Polygon', 'coordinates': [[[-122.26778447628023, 37.871211699952674], [-122.26777911186217, 37.87095762159011], [-122.26760745048522, 37.870983029465805], [-122.26759672164917, 37.87124557700147], [-122.26778447628023, 37.871211699952674]]]}}, {'type': 'Feature', 'properties': {'name': 'A

### Validating sensing settings

In [ ]:
for ss in spec_to_validate["sensing_settings"]:
    for phoneOS, compare_map in ss.items():
        compare_list = compare_map["compare"]
        for i, ssc in enumerate(compare_map["sensing_configs"]):
            if ssc["id"] != compare_list[i]:
                print("Mismatch in sensing configurations for %s" % ss)